These are screens are those that I follow from: *What Works on Wall Street, Fourth Edition: The Classic Guide to the Best-Performing Investment Strategies of All Time.* 

This is just my interpretation of the books material.

**This material is not intended to be relied upon as a forecast, research or investment advice, and is not a recommendation. Past performance is not always indicative of future returns. I may or may not own stocks listed**

# R System Prep

Data was downloaded the day that I run this notebook. Data should be 1 market day old.

This sheet was run on: 

In [1]:
Sys.time()

[1] "2022-07-05 08:22:06 PDT"

First initialize R environment:

In [2]:
suppressPackageStartupMessages(library(tidyverse))
suppressPackageStartupMessages(library(tidyquant))
suppressPackageStartupMessages(library(rio))
suppressPackageStartupMessages(library(knitr))
suppressPackageStartupMessages(library(kableExtra))
suppressPackageStartupMessages(library(IRdisplay))
#library(kableExtra)

<!-- TEASER_END -->
Read Data

In [3]:
#setwd("D:/OneDrive/SITES/www.michaelghens.com/Rdocs")
universe <-
  read.csv(
    "STOCKS.TXT",
    header = FALSE,
    stringsAsFactors = FALSE,
    na.strings = '-9999999999.990'
  )

universe_names <-
  read.csv(
    "STOCKS_KEY.TXT",
    header = FALSE,
    stringsAsFactors = FALSE,
    na.strings = '-9999999999.990'
  )

names(universe) <- universe_names[, 2]
count1 <- nrow(universe)[1]

Fields imported:

In [4]:
universe_names[, 2] %>%
  kbl("html") %>%
  as.character() %>%
  display_html()

x 
 
 
 
 
 Ticker 
 
 
 Company name 
 
 
 Price Change 52 week 
 
 
 Yield 
 
 
 Sector 
 
 
 Industry 
 
 
 Exchange 
 
 
 ADR/ADS Stock 
 
 
 Market Cap Q1 
 
 
 Price Change 13 week 
 
 
 Price Change 26 week 
 
 
 Cash flow/share 12m 
 
 
 Shares Average Q1 
 
 
 Sales 12m 
 
 
 Buyback Yield 
 
 
 Price/Book 
 
 
 PE 
 
 
 Price/Sales 
 
 
 Enterprise Value/EBITDA 
 
 
 Price/CFPS 
 
 
 Shareholder Yield 
 
 
 1yr chg debt 
 
 
 External Financing 
 
 
 LT Debt/equity Q1 
 
 
 LT debt/free cash flow 12m 
 
 
 EarningsQuality

Fields:

* EarningsQuality: ([Cash from operations 12m]-[Net income 12m])/[Market Cap Q1]
* 1yr chg debt: [Long-term debt Q1]-[Long-term debt Q5])/[Long-term debt Q5]
* External Financing: [Cash from financing Q1]/[Total assets Q1]

Are caculated fields


To clean up the universe of stocks, they must:

* have a ticker
* market cap
* 13,26,52 week price change
* not be over the counter
* not an ADR stock
* not be a reit stock.
* not be a closed end fund (TBA)

In [5]:
universe <- universe[complete.cases(universe$Ticker),]
universe <- universe[complete.cases(universe$`Market Cap Q1`),]
universe <- universe[complete.cases(universe$`Price Change 13 week`),]
universe <- universe[complete.cases(universe$`Price Change 26 week`),]
universe <- universe[complete.cases(universe$`Price Change 52 week`),]
#exchanges
condition <- c("N - New York", "A - American", "M - Nasdaq")
universe <- filter(universe, Exchange %in% condition)
universe <- filter(universe,`ADR/ADS Stock` == 'FALSE')
universe <- filter(universe,!grepl('REITs',Industry))
count2 <- nrow(universe)[1]

# Market Cap Variables

Screens need some market cap and momentom constants

* Minimum deflated Market Cap all cap universe
* Mediam 13 and 26 Momentom for bear trap
* Average Market cap for large cap universe

Calculating deflator, mins, means and medians.

In [6]:
options("getSymbols.warning4.0"=FALSE)
#find inflation Market Cap 150 @ 1995
getSymbols("CPIAUCSL", src = "FRED", auto.assign=getOption('getSymbols.auto.assign',TRUE))
deflator  <-
  last(Cl(to.yearly(CPIAUCSL)))[[1]] / Cl(to.yearly(CPIAUCSL))['1995'][[1]]
mincap <- 150 * deflator
median13w <- median(universe$`Price Change 13 week`)
median26w <- median(universe$`Price Change 26 week`)
avgmcap <- mean(universe$`Market Cap Q1`,  na.rm = TRUE)
avgshares <- mean(universe$`Shares Average Q1`,  na.rm = TRUE)
avgcashflowshares <- mean(universe$`Cash flow/share 12m`,  na.rm = TRUE)
avgsales15 <- mean(universe$`Sales 12m`,  na.rm = TRUE) * 1.5

[1] "CPIAUCSL"

# Create stock unverses

Screens are based on thre inverses of stocks 

* smallstocks
* allstocks
* largestocks
* marketleaders

## Create means and medians 

In [7]:
smallstocks <- filter(universe, `Market Cap Q1` <= avgmcap & `Market Cap Q1` >= mincap)

allstocks <- filter(universe, `Market Cap Q1` >= mincap)

largestocks <- filter(universe, `Market Cap Q1` >= avgmcap)

marketleaders <- allstocks %>% filter(Sector != "59  - Utilities") %>% 
  filter(`Shares Average Q1` > avgshares) %>%
  filter(`Cash flow/share 12m` > avgcashflowshares) %>%
  filter(`Sales 12m` > avgsales15)

Function to add rankings

In [8]:
calcvc2 <- function(x) {
  #Calculate VC2
  #subtract ntile from 101 to reverse (correct) Order. So Small is big
  x$`Price/Book.Rank` <-
    100 - round(percent_rank(x$`Price/Book`) * 100, 1)
  x$PE.Rank <- 100 - round(percent_rank(x$PE) * 100, 1)
  x$`Price/Sales.Rank` <-
    100 - round(percent_rank(x$`Price/Sales`) * 100, 1)
  x$`Enterprise Value/EBITDA.Rank` <-
    100 - round(percent_rank(x$`Enterprise Value/EBITDA`) * 100, 1)
  x$`Price/CFPS.Rank` <-
    100 - round(percent_rank(x$`Price/CFPS`) * 100, 1)
  x$`Shareholder Yield.Rank` <-
    round(percent_rank(x$`Shareholder Yield`) * 100, 1)
  
  #Stocks with no rank get 50
  x$`Price/Book.Rank`[is.na(x$`Price/Book.Rank`)] <- 50
  x$PE.Rank[is.na(x$PE.Rank)] <- 50
  x$`Price/Sales.Rank`[is.na(x$`Price/Sales.Rank`)] <- 50
  x$`Enterprise Value/EBITDA.Rank`[is.na(x$`Enterprise Value/EBITDA.Rank`)] <-
    50
  x$`Price/CFPS.Rank`[is.na(x$`Price/CFPS.Rank`)] <- 50
  x$`Shareholder Yield.Rank`[is.na(x$`Shareholder Yield.Rank`)] <- 50
  #Sum the Ranks
  x$SumRank <-
    x$`Price/Book.Rank` + x$PE.Rank + x$`Price/Sales.Rank` + x$`Enterprise Value/EBITDA.Rank` + x$`Price/CFPS.Rank` + x$`Shareholder Yield.Rank`
  x$VC2 <- round(percent_rank(x$SumRank) * 100, 1)
  return(x)
}

allstocks <- calcvc2(allstocks)
largestocks <- calcvc2(largestocks)
marketleaders <- calcvc2(marketleaders)

## Market Cap discriptive

In [9]:
summary(select_if(allstocks,is.numeric))

 Price Change 52 week     Yield        Market Cap Q1       Price Change 13 week
 Min.   :-93.82       Min.   : 0.000   Min.   :    284.1   Min.   :-81.67      
 1st Qu.:-40.62       1st Qu.: 0.000   1st Qu.:    649.8   1st Qu.:-25.71      
 Median :-16.60       Median : 0.000   Median :   1869.5   Median :-13.58      
 Mean   :-18.17       Mean   : 1.334   Mean   :  13516.4   Mean   :-14.95      
 3rd Qu.:  1.13       3rd Qu.: 2.100   3rd Qu.:   6283.4   3rd Qu.: -2.15      
 Max.   :376.06       Max.   :51.600   Max.   :2212838.0   Max.   :179.74      
                                                                               
 Price Change 26 week Cash flow/share 12m Shares Average Q1  
 Min.   :-91.290      Min.   :-181.0900   Min.   :    1.161  
 1st Qu.:-34.930      1st Qu.:  -1.2700   1st Qu.:   39.012  
 Median :-18.900      Median :  -0.0400   Median :   74.786  
 Mean   :-18.084      Mean   :  -0.3836   Mean   :  210.748  
 3rd Qu.: -0.815      3rd Qu.:   0.5800   3rd Qu.:

In [10]:
summary(largestocks$`Market Cap Q1`)

   Min. 1st Qu.  Median    Mean 3rd Qu.    Max. 
   8704   14291   24204   58162   47937 2212838 

In [11]:
summary(marketleaders$`Market Cap Q1`)

   Min. 1st Qu.  Median    Mean 3rd Qu.    Max. 
   1268   17521   38868   80640   77582 1920840 

# Portfolios

## Trending Value

In [12]:
TrendingValue <- allstocks %>%  filter(VC2 >= 90) %>% arrange(desc(`Price Change 26 week`)) %>% slice_head(n = 25) %>% select(Ticker, `Company name`,Sector,Industry)

TrendingValue %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 BTE 
 Baytex Energy Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 VHI 
 Valhi, Inc. 
 51 - Basic Materials 
 51101030 - Chemicals - Specialty 
 
 
 UFCS 
 United Fire Group, Inc. 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 GTE 
 Gran Tierra Energy Inc 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 CPG 
 Crescent Point Energy Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 LPG 
 Dorian LPG Ltd 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 UNM 
 Unum Group 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 IMO 
 Imperial Oil Ltd 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 MPC 
 Marathon Petroleum Corp 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 APA 
 APA Corp (US) 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 SENEA 
 Seneca Foods Corp 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 GOGL 
 Golden Ocean Group Ltd 
 52 - Industrials 
 52405020 - Freight & Logistics - Marine 
 
 
 CNX 
 CNX Resources Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 TGL 
 TransGlobe Energy Corporation 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 UAN 
 CVR Partners LP 
 51 - Basic Materials 
 51101020 - Chemicals - Agricultural 
 
 
 DSX 
 Diana Shipping Inc 
 52 - Industrials 
 52405020 - Freight & Logistics - Marine 
 
 
 HCC 
 Warrior Met Coal Inc 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 GNK 
 Genco Shipping & Trading Limit 
 52 - Industrials 
 52405020 - Freight & Logistics - Marine 
 
 
 NRP 
 Natural Resource Partners LP 
 50 - Energy 
 50101010 - Coal 
 
 
 KELYA 
 Kelly Services, Inc. 
 52 - Industrials 
 52203030 - Employment Services 
 
 
 SAFM 
 Sanderson Farms, Inc. 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 T 
 AT&T Inc. 
 57 - Technology 
 57401020 - Telecommunications Services - Wireless 
 
 
 ZEUS 
 Olympic Steel, Inc. 
 51 - Basic Materials 
 51201020 - Metals & Mining - Iron & Steel 
 
 
 MERC 
 Mercer International Inc. 
 51 - Basic Materials 
 51301020 - Paper Products 
 
 
 CAL 
 Caleres Inc 
 53 - Consumer Cyclicals 
 53403040 - Retailers - Apparel & Accessories

## Cheap Stocks on the mend

In [13]:
cheapmend <-
  allstocks %>%  filter(VC2 >= 70) %>% filter(`Price Change 13 week` > median13w) %>% filter(`Price Change 26 week` >
                                        median26w) %>% arrange(desc(`Price Change 26 week`)) %>%             
                                        slice_head(n = 25) %>% select(Ticker, `Company name`)

cheapmend %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 
 
 
 
 PBF 
 PBF Energy Inc 
 
 
 HMLP 
 Hoegh LNG Partners LP 
 
 
 EGY 
 VAALCO Energy, Inc. 
 
 
 CEIX 
 Consol Energy Inc 
 
 
 AMR 
 Alpha Metallurgical Resources 
 
 
 BTU 
 Peabody Energy Corporation 
 
 
 CVI 
 CVR Energy, Inc. 
 
 
 OBE 
 Obsidian Energy Ltd 
 
 
 BTE 
 Baytex Energy Corp 
 
 
 VHI 
 Valhi, Inc. 
 
 
 TRQ 
 Turquoise Hill Resources Ltd 
 
 
 NBR 
 Nabors Industries Ltd. 
 
 
 ARCH 
 Arch Resources Inc 
 
 
 CVE 
 Cenovus Energy Inc (US) 
 
 
 VET 
 Vermilion Energy Inc 
 
 
 SD 
 SandRidge Energy Inc. 
 
 
 ARLP 
 Alliance Resource Partners, L. 
 
 
 BMEA 
 Biomea Fusion Inc 
 
 
 MTOR 
 Meritor Inc 
 
 
 UFCS 
 United Fire Group, Inc. 
 
 
 ULH 
 Universal Logistics Holdings I 
 
 
 VLO 
 Valero Energy Corporation 
 
 
 XOM 
 Exxon Mobil Corp 
 
 
 SU 
 Suncor Energy Inc. (USA) 
 
 
 CNR 
 Cornerstone Building Brands In

## Market Leaders

### Price Appreciation

In [14]:
mlsy <- marketleaders %>% filter(`Price Change 13 week` > median13w) %>% 
  filter(`Price Change 26 week` >median26w) %>% 
  arrange(desc(`Shareholder Yield`)) %>%
  slice_head(n = 25) %>% 
  select(Ticker, `Company name`,Sector,Industry)
mlsy %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 HPQ 
 HP Inc 
 57 - Technology 
 57106010 - Computer Hardware 
 
 
 MPC 
 Marathon Petroleum Corp 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 LUMN 
 Lumen Technologies Inc 
 57 - Technology 
 57401010 - Telecommunications Services - Integrated 
 
 
 MPLX 
 MPLX LP 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 IMO 
 Imperial Oil Ltd 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 PAA 
 Plains All American Pipeline, 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 ALL 
 Allstate Corp 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 MET 
 Metlife Inc 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 SU 
 Suncor Energy Inc. (USA) 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 HIG 
 Hartford Financial Services Gr 
 55 - Financials 
 55301010 - Insurance - Multiline & Brokers 
 
 
 PFG 
 Principal Financial Group Inc 
 55 - Financials 
 55102020 - Investment Management & Fund Operators 
 
 
 PAGP 
 Plains GP Holdings LP 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 AMGN 
 Amgen, Inc. 
 56 - Healthcare 
 56201040 - Pharmaceuticals 
 
 
 DVN 
 Devon Energy Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 EPD 
 Enterprise Products Partners L 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 L 
 Loews Corporation 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 CB 
 Chubb Ltd 
 55 - Financials 
 55301010 - Insurance - Multiline & Brokers 
 
 
 LYB 
 LyondellBasell Industries NV 
 51 - Basic Materials 
 51101010 - Chemicals - Commodity 
 
 
 MS 
 Morgan Stanley 
 55 - Financials 
 55102010 - Investment Banking & Brokerage Services 
 
 
 AMCR 
 Amcor PLC 
 51 - Basic Materials 
 51302010 - Non-Paper Containers & Packaging 
 
 
 BMY 
 Bristol-Myers Squibb Co 
 56 - Healthcare 
 56201040 - Pharmaceuticals 
 
 
 ACGL 
 Arch Capital Group Ltd. 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 TRV 
 Travelers Companies Inc 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 ENLC 
 EnLink Midstream LLC 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 AON 
 Aon PLC 
 55 - Financials 
 55301010 - Insurance - Multiline & Brokers

In [15]:
mlvc2 <- marketleaders %>% filter(`Price Change 13 week` > median13w) %>% 
  filter(`Price Change 26 week` >median26w) %>% 
  arrange(desc(VC2)) %>%
  slice_head(n = 25) %>% 
  select(Ticker, `Company name`,Sector,Industry)
mlvc2 %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 LUMN 
 Lumen Technologies Inc 
 57 - Technology 
 57401010 - Telecommunications Services - Integrated 
 
 
 MET 
 Metlife Inc 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 IMO 
 Imperial Oil Ltd 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 T 
 AT&T Inc. 
 57 - Technology 
 57401020 - Telecommunications Services - Wireless 
 
 
 HPQ 
 HP Inc 
 57 - Technology 
 57106010 - Computer Hardware 
 
 
 HIG 
 Hartford Financial Services Gr 
 55 - Financials 
 55301010 - Insurance - Multiline & Brokers 
 
 
 LYB 
 LyondellBasell Industries NV 
 51 - Basic Materials 
 51101010 - Chemicals - Commodity 
 
 
 L 
 Loews Corporation 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 MPC 
 Marathon Petroleum Corp 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 ALL 
 Allstate Corp 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 ORI 
 Old Republic International Cor 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 PFG 
 Principal Financial Group Inc 
 55 - Financials 
 55102020 - Investment Management & Fund Operators 
 
 
 TSN 
 Tyson Foods, Inc. 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 SU 
 Suncor Energy Inc. (USA) 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 ACGL 
 Arch Capital Group Ltd. 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 TEVA 
 Teva Pharmaceutical Industries 
 56 - Healthcare 
 56201040 - Pharmaceuticals 
 
 
 GS 
 Goldman Sachs Group Inc 
 55 - Financials 
 55102010 - Investment Banking & Brokerage Services 
 
 
 TRV 
 Travelers Companies Inc 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 PAGP 
 Plains GP Holdings LP 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 VTRS 
 Viatris Inc 
 56 - Healthcare 
 56201040 - Pharmaceuticals 
 
 
 PAA 
 Plains All American Pipeline, 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 ET 
 Energy Transfer LP 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 WRK 
 Westrock Co 
 51 - Basic Materials 
 51302020 - Paper Packaging 
 
 
 MS 
 Morgan Stanley 
 55 - Financials 
 55102010 - Investment Banking & Brokerage Services 
 
 
 RCI.B 
 Rogers Communications Inc. 
 57 - Technology 
 57401020 - Telecommunications Services - Wireless

In [16]:
unique(arrange(rbind(mlvc2,mlsy),Ticker)) %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 1 
 ACGL 
 Arch Capital Group Ltd. 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 3 
 ALL 
 Allstate Corp 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 5 
 AMCR 
 Amcor PLC 
 51 - Basic Materials 
 51302010 - Non-Paper Containers & Packaging 
 
 
 6 
 AMGN 
 Amgen, Inc. 
 56 - Healthcare 
 56201040 - Pharmaceuticals 
 
 
 7 
 AON 
 Aon PLC 
 55 - Financials 
 55301010 - Insurance - Multiline & Brokers 
 
 
 8 
 BMY 
 Bristol-Myers Squibb Co 
 56 - Healthcare 
 56201040 - Pharmaceuticals 
 
 
 9 
 CB 
 Chubb Ltd 
 55 - Financials 
 55301010 - Insurance - Multiline & Brokers 
 
 
 10 
 DVN 
 Devon Energy Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 11 
 ENLC 
 EnLink Midstream LLC 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 12 
 EPD 
 Enterprise Products Partners L 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 13 
 ET 
 Energy Transfer LP 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 14 
 GS 
 Goldman Sachs Group Inc 
 55 - Financials 
 55102010 - Investment Banking & Brokerage Services 
 
 
 15 
 HIG 
 Hartford Financial Services Gr 
 55 - Financials 
 55301010 - Insurance - Multiline & Brokers 
 
 
 17 
 HPQ 
 HP Inc 
 57 - Technology 
 57106010 - Computer Hardware 
 
 
 19 
 IMO 
 Imperial Oil Ltd 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 21 
 L 
 Loews Corporation 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 23 
 LUMN 
 Lumen Technologies Inc 
 57 - Technology 
 57401010 - Telecommunications Services - Integrated 
 
 
 25 
 LYB 
 LyondellBasell Industries NV 
 51 - Basic Materials 
 51101010 - Chemicals - Commodity 
 
 
 27 
 MET 
 Metlife Inc 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 29 
 MPC 
 Marathon Petroleum Corp 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 31 
 MPLX 
 MPLX LP 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 32 
 MS 
 Morgan Stanley 
 55 - Financials 
 55102010 - Investment Banking & Brokerage Services 
 
 
 34 
 ORI 
 Old Republic International Cor 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 35 
 PAA 
 Plains All American Pipeline, 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 37 
 PAGP 
 Plains GP Holdings LP 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 39 
 PFG 
 Principal Financial Group Inc 
 55 - Financials 
 55102020 - Investment Management & Fund Operators 
 
 
 41 
 RCI.B 
 Rogers Communications Inc. 
 57 - Technology 
 57401020 - Telecommunications Services - Wireless 
 
 
 42 
 SU 
 Suncor Energy Inc. (USA) 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 44 
 T 
 AT&T Inc. 
 57 - Technology 
 57401020 - Telecommunications Services - Wireless 
 
 
 45 
 TEVA 
 Teva Pharmaceutical Industries 
 56 - Healthcare 
 56201040 - Pharmaceuticals 
 
 
 46 
 TRV 
 Travelers Companies Inc 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 48 
 TSN 
 Tyson Foods, Inc. 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 49 
 VTRS 
 Viatris Inc 
 56 - Healthcare 
 56201040 - Pharmaceuticals 
 
 
 50 
 WRK 
 Westrock Co 
 51 - Basic Materials 
 51302020 - Paper Packaging

In [17]:
utilities <- allstocks %>%
  filter(Sector == "59  - Utilities") %>%
  arrange(desc(VC2)) %>%
  slice_head(n =25) %>% 
  select(Ticker, `Company name`,Sector,Industry)
  
noncyc <- filter(allstocks,Sector == "54  - Consumer Non-Cyclicals") %>%
  arrange(desc(`Shareholder Yield`)) %>%
  slice_head(n = 25) %>% 
  select(Ticker, `Company name`,Sector,Industry)
  
arrange(rbind(utilities,noncyc),Ticker)   %>%
  kable("html") %>%
  as.character() %>%
  display_html()

constap <- rbind(slice_head(noncyc,n=3),slice_head(utilities,n=3))

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 AGRO 
 Adecoagro SA 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 ALE 
 ALLETE Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 AVA 
 Avista Corp 
 59 - Utilities 
 59104010 - Utilities - Multiline 
 
 
 AY 
 Atlantica Sustainable Infrastr 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 BIPC 
 Brookfield Infrastructure Corp 
 59 - Utilities 
 59102010 - Utilities - Natural Gas 
 
 
 CAH 
 Cardinal Health Inc 
 54 - Consumer Non-Cyclicals 
 54301010 - Retailers - Drug 
 
 
 CLX 
 Clorox Co 
 54 - Consumer Non-Cyclicals 
 54201010 - Household Products 
 
 
 COKE 
 Coca-Cola Consolidated Inc 
 54 - Consumer Non-Cyclicals 
 54101030 - Non-Alcoholic Beverages 
 
 
 CSV 
 Carriage Services, Inc. 
 54 - Consumer Non-Cyclicals 
 54201030 - Personal Services 
 
 
 EIX 
 Edison International 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 ETR 
 Entergy Corporation 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 EVRG 
 Evergy Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 EXC 
 Exelon Corporation 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 HAIN 
 Hain Celestial Group Inc 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 HLF 
 Herbalife Nutrition Ltd 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 HRB 
 H & R Block Inc 
 54 - Consumer Non-Cyclicals 
 54201030 - Personal Services 
 
 
 KEN 
 Kenon Holdings Ltd 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 KR 
 Kroger Co 
 54 - Consumer Non-Cyclicals 
 54301020 - Food Retail & Distribution 
 
 
 MCK 
 McKesson Corporation 
 54 - Consumer Non-Cyclicals 
 54301010 - Retailers - Drug 
 
 
 MDU 
 Mdu Resources Group Inc 
 59 - Utilities 
 59104010 - Utilities - Multiline 
 
 
 MED 
 Medifast Inc 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 MIC 
 Macquarie Infrastructure Holdi 
 59 - Utilities 
 59102010 - Utilities - Natural Gas 
 
 
 MMM 
 3M Co 
 54 - Consumer Non-Cyclicals 
 54401010 - Consumer Goods Conglomerates 
 
 
 MO 
 Altria Group Inc 
 54 - Consumer Non-Cyclicals 
 54102030 - Tobacco 
 
 
 NRG 
 NRG Energy Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 NUS 
 Nu Skin Enterprises, Inc. 
 54 - Consumer Non-Cyclicals 
 54201020 - Personal Products 
 
 
 OGE 
 OGE Energy Corp. 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 OTTR 
 Otter Tail Corporation 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 PCG 
 PG&E Corporation 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 PETS 
 Petmed Express Inc 
 54 - Consumer Non-Cyclicals 
 54301010 - Retailers - Drug 
 
 
 PG 
 Procter & Gamble Co 
 54 - Consumer Non-Cyclicals 
 54201020 - Personal Products 
 
 
 PM 
 Philip Morris International In 
 54 - Consumer Non-Cyclicals 
 54102030 - Tobacco 
 
 
 PNM 
 PNM Resources Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 PNW 
 Pinnacle West Capital Corporat 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 POR 
 Portland General Electric Comp 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 PPL 
 PPL Corp 
 59 - Utilities 
 59104010 - Utilities - Multiline 
 
 
 PRG 
 PROG Holdings Inc 
 54 - Consumer Non-Cyclicals 
 54201030 - Personal Services 
 
 
 RNW 
 Renew Energy Global PLC 
 59 - Utilities 
 59101020 - Utilities - Independent Power Producers 
 
 
 SCI 
 Service Corporation Internatio 
 54 - Consumer Non-Cyclicals 
 54201030 - Personal Services 
 
 
 SENEA 
 Seneca Foods Corp 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 SFM 
 Sprouts Farmers Market Inc 
 54 - Consumer Non-Cyclicals 
 54301020 - Food Retail & Distribution 
 
 
 SR 
 Spire Inc 
 59 - Utilities 
 59102010 - Utilities - Natural Gas 
 
 
 SWX 
 Southwest Gas Holdings Inc 
 59 - Utilities 
 59102010 - Utilities - Natural Gas 
 
 
 TAC 
 TransAlta Corporation (USA) 
 59 - Utilities 
 59101020 - Utilities - Independent Power Producers 
 
 
 TPB 
 Turni

## My 24 stock port

In [18]:
n <-1
c <-1
while(c < 12)  {
  mlC <- unique(rbind(slice_head(mlvc2,n=n),slice_head(mlsy,n=n)))
  n <- n + 1
  c = nrow(mlC)
}

n <-1
c <-1
rportTemp <- rbind(slice_head(mlC, n=6),constap)
while(c < 25)  {

rport <- unique(rbind(rportTemp,slice_head(TrendingValue,n=n)))
  n <- n + 1
  c = nrow(rport)
}
rport %>%
  kable("html") %>%
  as.character() %>%
  display_html()

Ticker 
 Company name 
 Sector 
 Industry 
 
 
 
 
 1 
 LUMN 
 Lumen Technologies Inc 
 57 - Technology 
 57401010 - Telecommunications Services - Integrated 
 
 
 2 
 MET 
 Metlife Inc 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 3 
 IMO 
 Imperial Oil Ltd 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 4 
 T 
 AT&T Inc. 
 57 - Technology 
 57401020 - Telecommunications Services - Wireless 
 
 
 5 
 HPQ 
 HP Inc 
 57 - Technology 
 57106010 - Computer Hardware 
 
 
 6 
 HIG 
 Hartford Financial Services Gr 
 55 - Financials 
 55301010 - Insurance - Multiline & Brokers 
 
 
 7 
 COKE 
 Coca-Cola Consolidated Inc 
 54 - Consumer Non-Cyclicals 
 54101030 - Non-Alcoholic Beverages 
 
 
 8 
 PRG 
 PROG Holdings Inc 
 54 - Consumer Non-Cyclicals 
 54201030 - Personal Services 
 
 
 9 
 CSV 
 Carriage Services, Inc. 
 54 - Consumer Non-Cyclicals 
 54201030 - Personal Services 
 
 
 10 
 NRG 
 NRG Energy Inc 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 11 
 UGI 
 UGI Corp 
 59 - Utilities 
 59102010 - Utilities - Natural Gas 
 
 
 12 
 KEN 
 Kenon Holdings Ltd 
 59 - Utilities 
 59101010 - Utilities - Electric 
 
 
 13 
 BTE 
 Baytex Energy Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 14 
 VHI 
 Valhi, Inc. 
 51 - Basic Materials 
 51101030 - Chemicals - Specialty 
 
 
 15 
 UFCS 
 United Fire Group, Inc. 
 55 - Financials 
 55301020 - Insurance - Property & Casualty 
 
 
 16 
 GTE 
 Gran Tierra Energy Inc 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 17 
 CPG 
 Crescent Point Energy Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 18 
 LPG 
 Dorian LPG Ltd 
 50 - Energy 
 50103030 - Oil & Gas - Transportation Services 
 
 
 19 
 UNM 
 Unum Group 
 55 - Financials 
 55301030 - Insurance - Life & Health 
 
 
 21 
 MPC 
 Marathon Petroleum Corp 
 50 - Energy 
 50102030 - Oil & Gas - Refining and Marketing 
 
 
 22 
 APA 
 APA Corp (US) 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 23 
 SENEA 
 Seneca Foods Corp 
 54 - Consumer Non-Cyclicals 
 54102020 - Food Processing 
 
 
 24 
 GOGL 
 Golden Ocean Group Ltd 
 52 - Industrials 
 52405020 - Freight & Logistics - Marine 
 
 
 25 
 CNX 
 CNX Resources Corp 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production 
 
 
 26 
 TGL 
 TransGlobe Energy Corporation 
 50 - Energy 
 50102020 - Oil & Gas - Exploration and Production